# 01. Import Libraries and dataframe
# 02. Wrangle data for mapping
# 03. Clean data for mapping
# 04. Import map (JSON) to be used
# 05. Create choropleth maps
# 06. Discuss results

    1. Import libraries and dataframe

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib
import os
import folium
import json

In [2]:
#Ensure charts are displayed in notebook
%matplotlib inline

In [3]:
#define path for easy access
path = r'C:\Users\dodge\24-08-27 Transportation'

In [4]:
#Import current vehicles dataframe
df_cars= pd.read_csv(os.path.join(path, '02 Data', 'Prepared Data', 'cars_explored.csv'), index_col = 0)

In [5]:
df_cars.head(10)

Month_ending  Year     County State Primary_use  Battery_BEVs  \
0         April  2017      Pinal    AZ   Passenger             2   
1         April  2017     Island    WA   Passenger           108   
2         April  2017      Clark    WA       Truck             0   
3         April  2017  Allegheny    PA   Passenger             1   
4         April  2017     Shelby    TN   Passenger             0   
5         April  2017       Dale    AL   Passenger             0   
6         April  2017  Jefferson    WA   Passenger            98   
8         April  2017    Harnett    NC   Passenger             1   
9         April  2017  Salt Lake    UT   Passenger             0   
10        April  2017     Yakima    WA       Truck             0   

    Hybrid_(PHEVs)  EV_Total  Non-Electric_Total  Total_Veh  %_Electric  \
0                0         2                 254        256        0.78   
1              128       236               59768      60004        0.39   
2                0         0               77561      77561        0.00   
3                0         1                  93         94        1.06   
4                1         1                 109        110        0.91   
5                1         1                  65         66        1.52   
6               56       154               23744      23898        0.64   
8                0         1                 257        258        0.39   
9                1         1                 289        290        0.34   
10               0         0               57219      57219        0.00   

     Proximity  
0      Nearest  
1   Washington  
2   Washington  
3     Furthest  
4     Furthest  
5     Furthest  
6   Washington  
8     Furthest  
9      Nearest  
10  Washington

    2. Wrangle data for mapping purposes

In [6]:
df_cars.shape

(17886, 12)

In [7]:
#Add a column for State Names with proper lettering
states = {
        'AK': 'Alaska',
        'AL': 'Alabama',
        'AR': 'Arkansas',
        'AS': 'American Samoa',
        'AZ': 'Arizona',
        'CA': 'California',
        'CO': 'Colorado',
        'CT': 'Connecticut',
        'DC': 'District of Columbia',
        'DE': 'Delaware',
        'FL': 'Florida',
        'GA': 'Georgia',
        'GU': 'Guam',
        'HI': 'Hawaii',
        'IA': 'Iowa',
        'ID': 'Idaho',
        'IL': 'Illinois',
        'IN': 'Indiana',
        'KS': 'Kansas',
        'KY': 'Kentucky',
        'LA': 'Louisiana',
        'MA': 'Massachusetts',
        'MD': 'Maryland',
        'ME': 'Maine',
        'MI': 'Michigan',
        'MN': 'Minnesota',
        'MO': 'Missouri',
        'MP': 'Northern Mariana Islands',
        'MS': 'Mississippi',
        'MT': 'Montana',
        'NA': 'National',
        'NC': 'North Carolina',
        'ND': 'North Dakota',
        'NE': 'Nebraska',
        'NH': 'New Hampshire',
        'NJ': 'New Jersey',
        'NM': 'New Mexico',
        'NV': 'Nevada',
        'NY': 'New York',
        'OH': 'Ohio',
        'OK': 'Oklahoma',
        'OR': 'Oregon',
        'PA': 'Pennsylvania',
        'PR': 'Puerto Rico',
        'RI': 'Rhode Island',
        'SC': 'South Carolina',
        'SD': 'South Dakota',
        'TN': 'Tennessee',
        'TX': 'Texas',
        'UT': 'Utah',
        'VA': 'Virginia',
        'VI': 'Virgin Islands',
        'VT': 'Vermont',
        'WA': 'Washington',
        'WI': 'Wisconsin',
        'WV': 'West Virginia',
        'WY': 'Wyoming'
}

In [8]:
#Add a column to dataframe with full state names
def State_Names(state):
    return states[state]

df_cars['State_Names'] = df_cars['State'].apply(State_Names)

In [9]:
df_cars.head(10)

Month_ending  Year     County State Primary_use  Battery_BEVs  \
0         April  2017      Pinal    AZ   Passenger             2   
1         April  2017     Island    WA   Passenger           108   
2         April  2017      Clark    WA       Truck             0   
3         April  2017  Allegheny    PA   Passenger             1   
4         April  2017     Shelby    TN   Passenger             0   
5         April  2017       Dale    AL   Passenger             0   
6         April  2017  Jefferson    WA   Passenger            98   
8         April  2017    Harnett    NC   Passenger             1   
9         April  2017  Salt Lake    UT   Passenger             0   
10        April  2017     Yakima    WA       Truck             0   

    Hybrid_(PHEVs)  EV_Total  Non-Electric_Total  Total_Veh  %_Electric  \
0                0         2                 254        256        0.78   
1              128       236               59768      60004        0.39   
2                0         0               77561      77561        0.00   
3                0         1                  93         94        1.06   
4                1         1                 109        110        0.91   
5                1         1                  65         66        1.52   
6               56       154               23744      23898        0.64   
8                0         1                 257        258        0.39   
9                1         1                 289        290        0.34   
10               0         0               57219      57219        0.00   

     Proximity     State_Names  
0      Nearest         Arizona  
1   Washington      Washington  
2   Washington      Washington  
3     Furthest    Pennsylvania  
4     Furthest       Tennessee  
5     Furthest         Alabama  
6   Washington      Washington  
8     Furthest  North Carolina  
9      Nearest            Utah  
10  Washington      Washington

In [10]:
df_cars.shape

(17886, 13)

In [11]:
#Identify columns that will be used for mapping
df_cars.columns

Index(['Month_ending', 'Year', 'County', 'State', 'Primary_use',
       'Battery_BEVs', 'Hybrid_(PHEVs)', 'EV_Total', 'Non-Electric_Total',
       'Total_Veh', '%_Electric', 'Proximity', 'State_Names'],
      dtype='object')

In [12]:
#Limit columns being used
columns = ['County', 'Primary_use', 'EV_Total', 'Non-Electric_Total', '%_Electric', 'Proximity', 'State_Names']

In [13]:
df_cars_geo = df_cars[columns]

In [14]:
df_cars_geo.head()

County Primary_use  EV_Total  Non-Electric_Total  %_Electric  \
0      Pinal   Passenger         2                 254        0.78   
1     Island   Passenger       236               59768        0.39   
2      Clark       Truck         0               77561        0.00   
3  Allegheny   Passenger         1                  93        1.06   
4     Shelby   Passenger         1                 109        0.91   

    Proximity   State_Names  
0     Nearest       Arizona  
1  Washington    Washington  
2  Washington    Washington  
3    Furthest  Pennsylvania  
4    Furthest     Tennessee

In [15]:
df_cars_geo.shape

(17886, 7)

    3. Clean data for mapping

In [16]:
#Look for missing values

In [17]:
df_cars_geo.isnull().sum()

County                0
Primary_use           0
EV_Total              0
Non-Electric_Total    0
%_Electric            0
Proximity             0
State_Names           0
dtype: int64

In [18]:
#No missing values

In [19]:
#Limit columns pulling for map
map_data = df_cars[['State_Names', 'Total_Veh']]

In [20]:
map_data.head(10)

State_Names  Total_Veh
0          Arizona        256
1       Washington      60004
2       Washington      77561
3     Pennsylvania         94
4        Tennessee        110
5          Alabama         66
6       Washington      23898
8   North Carolina        258
9             Utah        290
10      Washington      57219

Looking at this makes me realize that the map will be disportionate to WA state and probably will not accurately reflect a distribution.  I think I need to separate the map by WA and non-WA, but will run a test map to see.

     04. Import map (JSON) to be used

In [21]:
#assign state JSON URL a geo-code
states_geo_url=('https://coach-courses-us.s3.amazonaws.com/public/courses/data-immersion/A6/6.3/us-states.json')

    5. Create Choropleth Maps

In [22]:
map1 = folium.Map(location = [40, -95], zoom_start = 4)

folium.Choropleth(
    geo_data = states_geo_url, 
    data = map_data,
    columns = ['State_Names', 'Total_Veh'],
    key_on = 'feature.properties.name',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Vehicle Registrations").add_to(map1)

folium.LayerControl().add_to(map1)

map1

As expected, no other state values showed up.  Will separate WA state from other states to look at their vehicle registration in the State of WA separately.

In [23]:
#Use proximity column to select states outside of WA state
df_cars_outside = df_cars[df_cars['Proximity']!='Washington']

In [24]:
df_cars_outside.head(10)

Month_ending  Year       County State Primary_use  Battery_BEVs  \
0         April  2017        Pinal    AZ   Passenger             2   
3         April  2017    Allegheny    PA   Passenger             1   
4         April  2017       Shelby    TN   Passenger             0   
5         April  2017         Dale    AL   Passenger             0   
8         April  2017      Harnett    NC   Passenger             1   
9         April  2017    Salt Lake    UT   Passenger             0   
11        April  2017   Montgomery    PA   Passenger             1   
14        April  2017         Utah    UT   Passenger             0   
20        April  2017  Los Angeles    CA   Passenger             3   
21        April  2017          Lee    AL   Passenger             1   

    Hybrid_(PHEVs)  EV_Total  Non-Electric_Total  Total_Veh  %_Electric  \
0                0         2                 254        256        0.78   
3                0         1                  93         94        1.06   
4                1         1                 109        110        0.91   
5                1         1                  65         66        1.52   
8                0         1                 257        258        0.39   
9                1         1                 289        290        0.34   
11               0         1                  41         42        2.38   
14               1         1                 164        165        0.61   
20               1         4                1345       1349        0.30   
21               0         1                  35         36        2.78   

   Proximity     State_Names  
0    Nearest         Arizona  
3   Furthest    Pennsylvania  
4   Furthest       Tennessee  
5   Furthest         Alabama  
8   Furthest  North Carolina  
9    Nearest            Utah  
11  Furthest    Pennsylvania  
14   Nearest            Utah  
20   Nearest      California  
21  Furthest         Alabama

In [25]:
df_cars_outside.shape

(11724, 13)

In [26]:
#Whoops--wrong dataframe
df_cars_out_geo = df_cars_outside[columns]

In [27]:
df_cars_out_geo.head(10)

County Primary_use  EV_Total  Non-Electric_Total  %_Electric  \
0         Pinal   Passenger         2                 254        0.78   
3     Allegheny   Passenger         1                  93        1.06   
4        Shelby   Passenger         1                 109        0.91   
5          Dale   Passenger         1                  65        1.52   
8       Harnett   Passenger         1                 257        0.39   
9     Salt Lake   Passenger         1                 289        0.34   
11   Montgomery   Passenger         1                  41        2.38   
14         Utah   Passenger         1                 164        0.61   
20  Los Angeles   Passenger         4                1345        0.30   
21          Lee   Passenger         1                  35        2.78   

   Proximity     State_Names  
0    Nearest         Arizona  
3   Furthest    Pennsylvania  
4   Furthest       Tennessee  
5   Furthest         Alabama  
8   Furthest  North Carolina  
9    Nearest            Utah  
11  Furthest    Pennsylvania  
14   Nearest            Utah  
20   Nearest      California  
21  Furthest         Alabama

In [28]:
#Map outside states 
map_out = folium.Map(location = [40, -95], zoom_start = 4)

folium.Choropleth(
    geo_data = states_geo_url, 
    data = df_cars_outside,
    columns = ['State_Names', 'Total_Veh'],
    key_on = 'feature.properties.name',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "Vehicle Registrations").add_to(map_out)

folium.LayerControl().add_to(map_out)

map_out

States that register vehicles in WA include Arizona, Nevada, Oregon, New York and North Carolina.

In [29]:
#Look at electric vehicle % outside of WA
map_electric = folium.Map(location = [40, -95], zoom_start = 4)

folium.Choropleth(
    geo_data = states_geo_url, 
    data = df_cars_out_geo,
    columns = ['State_Names', '%_Electric'],
    key_on = 'feature.properties.name',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "% Electric registered in WA").add_to(map_electric)

folium.LayerControl().add_to(map_electric)

map_electric

In [30]:
#Super interesting that Arkansas has the highest percentage of electric vehicles registered in WA state followed by Kentucky.

In [44]:
#Export visualization
map_electric.figure.savefig(os.path.join(path, '04 Analysis', 'Visualizations', 'US_Electric.png'))

AttributeError: 'Map' object has no attribute 'figure'

# Utilize counties by state map for Washington State

In [31]:
#Utilize counties map for Washington state
WA_county = r'C:\Users\dodge\OneDrive\Data Analytics\Achievement 6\washington-state-counties_.geojson'

In [32]:
WA_county

'C:\\Users\\dodge\\OneDrive\\Data Analytics\\Achievement 6\\washington-state-counties_.geojson'

In [33]:
df_cars_WA = df_cars[df_cars['State'] == 'WA']

In [34]:
df_cars_WA.head(15)

Month_ending  Year     County State Primary_use  Battery_BEVs  \
1         April  2017     Island    WA   Passenger           108   
2         April  2017      Clark    WA       Truck             0   
6         April  2017  Jefferson    WA   Passenger            98   
10        April  2017     Yakima    WA       Truck             0   
12        April  2017   Skamania    WA       Truck             0   
13        April  2017    Whitman    WA   Passenger             9   
15        April  2017      Clark    WA   Passenger           755   
16        April  2017      Adams    WA   Passenger             2   
17        April  2017   Franklin    WA   Passenger            27   
18        April  2017      Ferry    WA       Truck             0   
19        April  2017   San Juan    WA       Truck             0   
22        April  2017  Klickitat    WA   Passenger            22   
25        April  2017     Skagit    WA       Truck             1   
27        April  2017   San Juan    WA   Passenger            98   
30        April  2017      Adams    WA       Truck             0   

    Hybrid_(PHEVs)  EV_Total  Non-Electric_Total  Total_Veh  %_Electric  \
1              128       236               59768      60004        0.39   
2                0         0               77561      77561        0.00   
6               56       154               23744      23898        0.64   
10               0         0               57219      57219        0.00   
12               0         0                3874       3874        0.00   
13              19        28               21964      21992        0.13   
15             471      1226              298474     299700        0.41   
16               3         5               12128      12133        0.04   
17              47        74               55348      55422        0.13   
18               0         0                3549       3549        0.00   
19               0         0                5551       5551        0.00   
22              23        45               14768      14813        0.30   
25               0         1               31395      31396        0.00   
27              35       133               13479      13612        0.98   
30               0         0                5072       5072        0.00   

     Proximity State_Names  
1   Washington  Washington  
2   Washington  Washington  
6   Washington  Washington  
10  Washington  Washington  
12  Washington  Washington  
13  Washington  Washington  
15  Washington  Washington  
16  Washington  Washington  
17  Washington  Washington  
18  Washington  Washington  
19  Washington  Washington  
22  Washington  Washington  
25  Washington  Washington  
27  Washington  Washington  
30  Washington  Washington

In [35]:
#Start county-level mapping
map_WA = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=0.1,
    legend_name = "% Electric registered in WA").add_to(map_WA)

folium.LayerControl().add_to(map_WA)

map_WA

In [36]:
#Create subsets by year
df_cars_WA_17 = df_cars_WA[df_cars_WA['Year']==2017]
df_cars_WA_18 = df_cars_WA[df_cars_WA['Year']==2018]
df_cars_WA_19 = df_cars_WA[df_cars_WA['Year']==2019]
df_cars_WA_20 = df_cars_WA[df_cars_WA['Year']==2020]
df_cars_WA_21 = df_cars_WA[df_cars_WA['Year']==2021]
df_cars_WA_22 = df_cars_WA[df_cars_WA['Year']==2022]
df_cars_WA_23 = df_cars_WA[df_cars_WA['Year']==2023]

In [37]:
map_WA17e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_17,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2017").add_to(map_WA17e)

folium.LayerControl().add_to(map_WA17e)

map_WA17e

In [38]:
map_WA18e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_18,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2018").add_to(map_WA18e)

folium.LayerControl().add_to(map_WA18e)

map_WA18e

In [39]:
map_WA19e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_19,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2019").add_to(map_WA19e)

folium.LayerControl().add_to(map_WA19e)

map_WA19e

In [40]:
map_WA20e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_20,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2020").add_to(map_WA20e)

folium.LayerControl().add_to(map_WA20e)

map_WA20e

In [41]:
map_WA21e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_21,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2021").add_to(map_WA21e)

folium.LayerControl().add_to(map_WA21e)

map_WA21e

In [42]:
map_WA22e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_22,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2022").add_to(map_WA22e)

folium.LayerControl().add_to(map_WA22e)

map_WA22e

In [43]:
map_WA23e = folium.Map(location = [47, -120], zoom_start = 7)

folium.Choropleth(
    geo_data = WA_county, 
    data = df_cars_WA_23,
    columns = ['County', '%_Electric'],
    key_on = 'properties.NAME',
    fill_color = 'YlOrBr', fill_opacity=0.6, line_opacity=1.0,
    legend_name = "% Electric Vehicles registered in WA in 2023").add_to(map_WA23e)

folium.LayerControl().add_to(map_WA23e)

map_WA23e

It is really impressive to see the legend going up every year for the percentage of electric vehicles being registered in the state of Washington.  In 2017, the legend was 0 to 1.7, and in 2023 is 0 to 5.0 with more counties registering a percentage of those vehicles.  This is a starting point for answering the questions posed about the increase in percentages.